# NDIS Project - Azure OpenAI - PBSP Scoring - Page 4 - Restrictive interventions

In [ ]:
import os
import openai
import re
from ipywidgets import interact
import ipywidgets as widgets
from IPython.display import display, clear_output, Javascript, HTML, Markdown
import matplotlib.pyplot as plt
import matplotlib.ticker as mtick
import json
import spacy
from spacy import displacy
from dotenv import load_dotenv
import pandas as pd
import argilla as rg
from argilla.metrics.text_classification import f1
from typing import Dict
import warnings
warnings.filterwarnings('ignore')
%matplotlib inline
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_colwidth', 10000)
pd.set_option('display.width', 10000)

In [ ]:
#initializations
openai.api_key = os.environ['API_KEY']
openai.api_base = os.environ['API_BASE']
openai.api_type = os.environ['API_TYPE']
openai.api_version = os.environ['API_VERSION']
deployment_name = os.environ['DEPLOYMENT_ID']

#argilla
rg.init(
    api_url=os.environ["ARGILLA_API_URL"],
    api_key=os.environ["ARGILLA_API_KEY"]
)

In [ ]:
#sentence extraction
def extract_sentences(paragraph):
    symbols = ['\\.', '!', '\\?', ';', ':', ',', '\\_', '\n', '\\-']
    pattern = '|'.join([f'{symbol}' for symbol in symbols])
    sentences = re.split(pattern, paragraph)
    sentences = [sentence.strip() for sentence in sentences if sentence.strip()]
    return sentences

In [ ]:
def process_response(response, query):
    sentences = []
    topics = []
    scores = []
    lines = response.strip().split("\n")
    for line in lines:
        if "Restrictive interventions:" in line:
            topic = "RESTRICTIVE INTERVENTION"
        elif "None:" in line:
            topic = "NONE"
        else:
            try:
                phrase = line.split("(Confidence Score:")[0].strip()
                score = float(line.split("(Confidence Score:")[1].strip().replace(")", ""))
                sentences.append(phrase)
                topics.append(topic)
                scores.append(score)
            except:
                pass
    result_df = pd.DataFrame({'Phrase': sentences, 'Topic': topics, 'Score': scores})
    try:
        result_df['Phrase'] = result_df['Phrase'].str.replace('\d+\.', '', regex=True)
        result_df['Phrase'] = result_df['Phrase'].str.replace('^\s', '', regex=True)
    except:
        sentences = extract_sentences(query)
        topics = ['NONE'] * len(sentences)
        scores = [0.9] * len(sentences)
        result_df = pd.DataFrame({'Phrase': sentences, 'Topic': topics, 'Score': scores})
    return result_df

In [ ]:
def get_prompt(query):
    prompt = f"""
    Restrictive interventions refer to strategies or actions used to restrict a person's freedom of movement or autonomy in order to prevent them from harming themselves or others. These interventions are typically used as a last resort when all other de-escalation strategies have been exhausted and when there is an immediate risk of harm to the person or others. Examples of restrictive interventions may include physical restraint, seclusion, or the use of medication to manage behavior.

    Given the paragraph below in a behaviour support plan written by a disability practitioner, identify the phrases that represent restrictive interventions used with the person with disability.

    Paragraph:
    {query}

    All the following requirements must be met:
    - Provide your answer in a numbered list. 
    - All the phrases in your answer must be exact substrings in the original paragraph. without changing any characters.
    - All the upper case and lower case characters in the phrases in your answer must match the upper case and lower case characters in the original paragraph.
    - Start numbering the phrases from number 1.
    - Start your answer for the phrases with the title "Restrictive interventions:"
    - For each phrase in your answer, provide a confidence score that ranges between 0.50 and 1.00, where a score of 0.50 indicates you are very weakly confident that the phrase represents a restrictive intervention example, whereas a score of 1.00 indicates you are very strongly confident that the phrase represents a restrictive intervention example.
    - Include another numbered list titled "None:", which includes all the remaining phrases in the paragraph that do not represent any restrictive intervention examples. Provide a confidence score for each of these phrases as well.
    - There must not be any phrase in your answer that does not exist the paragraph above.
    - The below is an example paragraph and example answers. Follow them to help you with your answer. However, never use any of the phrases if it does not exist in the original paragraph above. 

    Example Paragraph:
    I am a disability practitioner who is managing Eddie, a person with autism. Eddie becomes upset because there is too much noise in the room, so I try to help Eddie calm down by removing him from the situation and giving him some quiet time in a different room. I also talk with Eddie about how he is feeling and what he needs to feel better. If these strategies do not work, I may consider using restrictive interventions such as gently holding Eddie's hand to prevent him from hurting himself or others. I may also use a weighted blanket or vest to calm Eddie down or provide a safe space for Eddie to limit his access to the environment and restrict his freedom of movement in order to prevent harm to himself or others. However, I will only use these strategies as a last resort and will do so in a way that is safe and respectful to Eddie.


    Example correct answer:

    Restrictive interventions:
    1. gently holding Eddie's hand to prevent him from hurting himself or others. (Confidence Score: 0.97)
    2. use a weighted blanket or vest to calm Eddie down. (Confidence Score: 0.95)
    3. provide a safe space for Eddie to limit his access to the environment and restrict his freedom of movement. (Confidence Score: 0.93)

    None:
    1. I am a disability practitioner who is managing Eddie, a person with autism, (Confidence Score: 0.99)
    2. Eddie becomes upset because there is too much noise in the room. (Confidence Score: 0.95)
    3. so I try to help Eddie calm down by removing him from the situation and giving him some quiet time in a different room. (Confidence Score: 0.94)
    4. I also talk with Eddie about how he is feeling and what he needs to feel better. (Confidence Score: 0.93)
    5. If these strategies do not work, I may consider using restrictive interventions such as (Confidence Score: 0.91)
    """
    return prompt

In [ ]:
def get_response_chatgpt(prompt):
    response=openai.ChatCompletion.create(   
        engine=deployment_name,   
        messages=[         
        {"role": "system", "content": "You are a helpful assistant."},                  
        {"role": "user", "content": prompt}     
        ],
        temperature=0
    )
    reply = response["choices"][0]["message"]["content"]
    return reply

In [ ]:
def custom_f1(data: Dict[str, float], title: str):
    from plotly.subplots import make_subplots
    import plotly.colors
    import random

    fig = make_subplots(
        rows=2,
        cols=1,
        subplot_titles=[        "Overall Model Score",        "Model Score By Category",    ],
    )

    x = ['precision', 'recall', 'f1']
    macro_data = [v for k, v in data.items() if "macro" in k]
    fig.add_bar(
        x=x,
        y=macro_data,
        row=1,
        col=1,
    )
    per_label = {
        k: v
        for k, v in data.items()
        if all(key not in k for key in ["macro", "micro", "support"])
    }

    num_labels = int(len(per_label.keys())/3)
    fixed_colors = [str(color) for color in plotly.colors.qualitative.Plotly]
    colors = random.sample(fixed_colors, num_labels)

    fig.add_bar(
        x=[k for k, v in per_label.items()],
        y=[v for k, v in per_label.items()],
        row=2,
        col=1,
        marker_color=[colors[int(i/3)] for i in range(0, len(per_label.keys()))]
    )
    fig.update_layout(showlegend=False, title_text=title)

    return fig

In [ ]:
def convert_df(result_df):
    new_df = pd.DataFrame(columns=['text', 'prediction'])
    new_df['text'] = result_df['Phrase']
    new_df['prediction'] = result_df.apply(lambda row: [[row['Topic'], row['Score']]], axis=1)
    return new_df

In [ ]:
topic_color_dict = {
        'RESTRICTIVE INTERVENTION': '#90EE90',
        'NONE': '#F08080'
    }

def color(df, color):
    return df.style.format({'Score': '{:,.2%}'.format}).bar(subset=['Score'], color=color)

def annotate_query(highlights, query, topics):
    ents = []
    for h, t in zip(highlights, topics):
        ent_dict = {}
        for match in re.finditer(h, query, re.IGNORECASE):
            ent_dict = {"start": match.start(), "end": match.end(), "label": t}
            break
        if len(ent_dict.keys()) > 0:
            ents.append(ent_dict)
    return ents

def path_to_image_html(path):
    return path

passing_score = 0.75
final_passing = 0.0
def display_final_df(agg_df):
    crits = [
            'RESTRICTIVE INTERVENTION'
        ]
    if not isinstance(agg_df, str):
        tags = []
        orig_crits = crits
        crits = [x for x in crits if x in agg_df.index.tolist()]
        bools = [agg_df.loc[crit, 'Final_Score'] > final_passing for crit in crits]
        paths = ['YES' if x else 'NO' for x in bools]
        df = pd.DataFrame({'Restrictive intervention': crits, 'USED': paths})
        rem_crits = [x for x in orig_crits if x not in crits]
        if len(rem_crits) > 0:
            df2 = pd.DataFrame({'Restrictive intervention': rem_crits, 'USED': ['NO'] * len(rem_crits)})
            df = pd.concat([df, df2])
    else:
        df = pd.DataFrame({'Restrictive intervention': [crits[0]], 'USED': ['NO']})
    df = df.set_index('Restrictive intervention')
    pd.set_option('display.max_colwidth', None)
    display(HTML('<div style="text-align: center;">' + df.to_html(classes=["align-center"], index=True, escape=False ,formatters=dict(USED=path_to_image_html)) + '</div>'))
    

### Please outline the strategies that will be implemented to de-escalate the person with disability’s challenging behaviours. <font color='red'>Please do not propose any restrictive practices (e.g., seclusion, restraint)</font>

In [ ]:
#demo with Voila

bhvr_label = widgets.Label(value='Please type your answer:')
bhvr_text_input = widgets.Textarea(
    value='',
    placeholder='Type your answer',
    description='',
    disabled=False,
    layout={'height': '300px', 'width': '90%'}
)

bhvr_nlp_btn = widgets.Button(
    description='Score Answer',
    disabled=False,
    button_style='success', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Score Answer',
    icon='check',
    layout={'height': '70px', 'width': '250px'}
)
bhvr_agr_btn = widgets.Button(
    description='Validate Data',
    disabled=False,
    button_style='success', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Validate Data',
    icon='check',
    layout={'height': '70px', 'width': '250px'}
)
bhvr_eval_btn = widgets.Button(
    description='Evaluate Model',
    disabled=False,
    button_style='success', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Evaluate Model',
    icon='check',
    layout={'height': '70px', 'width': '250px'}
)
btn_box = widgets.HBox([bhvr_nlp_btn, bhvr_agr_btn, bhvr_eval_btn], 
                       layout={'width': '100%', 'height': '160%'})
bhvr_outt = widgets.Output()
bhvr_outt.layout.height = '100%'
bhvr_outt.layout.width = '100%'
bhvr_box = widgets.VBox([bhvr_text_input, btn_box, bhvr_outt], 
                   layout={'width': '100%', 'height': '160%'})
dataset_rg_name = 'pbsp-page4-restrict-argilla-ds'
dataset_rg_url = f'http://localhost:6900/datasets/argilla/{dataset_rg_name}'
agrilla_df = None
annotated = False
def on_bhvr_button_next(b):
    global agrilla_df
    with bhvr_outt:
        clear_output()
        query = bhvr_text_input.value
        prompt = get_prompt(query)
        response = get_response_chatgpt(prompt)
        result_df = process_response(response, query)
        sub_result_df = result_df[(result_df['Score'] >= passing_score) & (result_df['Topic'] != 'NONE')]
        sub_2_result_df = result_df[result_df['Topic'] == 'NONE']
        highlights = []
        if len(sub_result_df) > 0:
            highlights = sub_result_df['Phrase'].tolist()
            highlight_topics = sub_result_df['Topic'].tolist()    
            ents = annotate_query(highlights, query, highlight_topics)
            colors = {}
            for ent, ht in zip(ents, highlight_topics):
                colors[ent['label']] = topic_color_dict[ht]

            ex = [{"text": query,
                   "ents": ents,
                   "title": None}]
            title = "Restrictive intervention Highlights"
            display(HTML(f'<center><h1>{title}</h1></center>'))
            html = displacy.render(ex, style="ent", manual=True, jupyter=True, options={'colors': colors})
            display(HTML(html))
            title = "Restrictive intervention Classifications"
            display(HTML(f'<center><h1>{title}</h1></center>'))
            for top in topic_color_dict.keys():
                top_result_df = sub_result_df[sub_result_df['Topic'] == top]
                if len(top_result_df) > 0:
                    top_result_df = top_result_df.sort_values(by='Score', ascending=False).reset_index(drop=True)
                    top_result_df = top_result_df.set_index('Phrase')
                    top_result_df = top_result_df[['Score']]
                    display(HTML(
                        f'<left><h2 style="text-decoration: underline; text-decoration-color:{topic_color_dict[top]};">{top}</h2></left>'))
                    display(color(top_result_df, topic_color_dict[top]))
            
            agg_df = sub_result_df.groupby('Topic')['Score'].sum()
            agg_df = agg_df.to_frame()
            agg_df.index.name = 'Topic'
            agg_df.columns = ['Total Score']
            agg_df = agg_df.assign(
                Final_Score=lambda x: x['Total Score'] / x['Total Score'].sum() * 100.00
            )
            agg_df = agg_df.sort_values(by='Final_Score', ascending=False)
            agg_df['Topic'] = agg_df.index
            rem_topics= [x for x in list(topic_color_dict.keys()) if not x in agg_df.Topic.tolist()]
            if len(rem_topics) > 0:
                rem_agg_df = pd.DataFrame({'Topic': rem_topics, 'Final_Score': 0.0, 'Total Score': 0.0})
                agg_df = pd.concat([agg_df, rem_agg_df])
            title = "Final Scores"
            display(HTML(f'<left><h1>{title}</h1></left>'))
            display_final_df(agg_df)
            if len(sub_2_result_df) > 0:
                sub_result_df = pd.concat([sub_result_df, sub_2_result_df]).reset_index(drop=True)
            agrilla_df = sub_result_df.copy()
        else:
            print(query)
            display_final_df('None')
            if len(sub_2_result_df) > 0:
                agrilla_df = sub_2_result_df.copy()

def on_agr_button_next(b):
    global agrilla_df, annotated
    with bhvr_outt:
        clear_output()
        if agrilla_df is not None:
            # convert the dataframe to the structure accepted by argilla
            converted_df = convert_df(agrilla_df)
            # convert pandas dataframe to DatasetForTextClassification
            dataset_rg = rg.DatasetForTextClassification.from_pandas(converted_df)
            # delete the old DatasetForTextClassification from the Argilla web app if exists
            rg.delete(dataset_rg_name, workspace="admin")
            # load the new DatasetForTextClassification into the Argilla web app
            rg.log(dataset_rg, name=dataset_rg_name, workspace="admin")
            # Make sure all classes are present for annotation
            rg_settings = rg.TextClassificationSettings(label_schema=list(topic_color_dict.keys()))
            rg.configure_dataset(name=dataset_rg_name, workspace="admin", settings=rg_settings)
            annotated = True
        else:
            display(Markdown("<h2 style='color:red; text-align:center;'>Please score the answer first!</h2>"))
            
def on_eval_button_next(b):
    global annotated
    with bhvr_outt:
        clear_output()
        if annotated:
            data = dict(f1(dataset_rg_name))['data']
            display(custom_f1(data, "Model Evaluation Results"))
        else:
            display(Markdown("<h2 style='color:red; text-align:center;'>Please score the answer and validate the data first!</h2>"))

bhvr_nlp_btn.on_click(on_bhvr_button_next)
bhvr_agr_btn.on_click(on_agr_button_next)
bhvr_eval_btn.on_click(on_eval_button_next)

display(bhvr_label, bhvr_box)